In [1]:
#!pip install scikit-learn==0.23.1

In [1]:
import numpy as np
import pandas as pd
import re
import sklearn
import nltk
import gensim
import matplotlib.pyplot as plt
import pyLDAvis
import pyLDAvis.gensim

from sklearn.model_selection import train_test_split, GridSearchCV
from sklearn.feature_extraction.text import CountVectorizer
from sklearn.feature_extraction.text import TfidfVectorizer
from sklearn.metrics import confusion_matrix, precision_score, precision_recall_curve, recall_score, f1_score, classification_report
from sklearn.linear_model import LogisticRegression
from sklearn.decomposition import LatentDirichletAllocation

from nltk.stem import WordNetLemmatizer
from nltk.stem.porter import *

from gensim.utils import simple_preprocess
from gensim.parsing.preprocessing import STOPWORDS
from gensim.corpora import Dictionary
from gensim.models import TfidfModel, LdaMulticore

# Data cleaning and splitting

In [2]:
#import dataset, remove the 'link' column and no match' rows
song_data = pd.read_csv("subsongdata_57650.csv")
song_data = song_data[['artist','song','text','explicit_label']]
song_data = song_data.loc[song_data['explicit_label'] != 'no match']

In [3]:
#remove'\n' from the lyrics
re_drop = re.compile(r'\n')        
song_data[['text']] = song_data[['text']].applymap(lambda x:re_drop.sub(' ',x))
song_data

artist                                             song  \
1       ABBA                                 Andante, Andante   
2       ABBA                                   As Good As New   
4       ABBA                                 Bang-A-Boomerang   
7       ABBA                                       Chiquitita   
11      ABBA                                    Dancing Queen   
...      ...                                              ...   
57593    Zao  To Think Of You Is To Treasure An Absent Memory   
57605  Zebra                                 As I Said Before   
57608  Zebra                          Hard Living Without You   
57609  Zebra                               When You Get There   
57612  Zebra                    You're Only Losing Your Heart   

                                                    text explicit_label  
1      Take it easy with me, please   Touch me gently...          False  
2      I'll never know why I had to go   Why I had to...          False  
4      Making somebody happy is a question of give an...          False  
7      Chiquitita, tell me what's wrong   You're ench...          False  
11     You can dance, you can jive, having the time o...          False  
...                                                  ...            ...  
57593  When you shut your eyes and fell asleep   Dark...          False  
57605  And I said before   I don't want no more   And...          False  
57608  Nothing to say no place to hide   I can't find...          False  
57609  You wake up in the morning   And you're not fe...          False  
57612  Don't' do anything I wouldn't do   Pass me any...          False  

[24676 rows x 4 columns]

In [4]:
#extract all the rows with explicit_label = True
song_data_1 = song_data.loc[song_data['explicit_label'] == 'True']
song_data_1

artist                        song  \
128     Adam Sandler                  Mr. Bake-O   
129     Adam Sandler      Steve Polychronopolous   
909    Avril Lavigne  Here's To Never Growing Up   
929    Avril Lavigne                 Rock N Roll   
2089      Bruno Mars                    Treasure   
...              ...                         ...   
57544           Z-Ro              Gripping Grain   
57545           Z-Ro         Guerilla Till I Die   
57550           Z-Ro            Lord Tell Me Why   
57560           Z-Ro          Talkin' Down On Me   
57561           Z-Ro             That'z Who I Am   

                                                    text explicit_label  
128             I'm sitting in my chair watching the ...           True  
129    I'm a big fuckin' dick   I'm a pain in your as...           True  
909    Singing Radiohead at the top of our lungs   Wi...           True  
929    Let them know that we're still rock n roll   I...           True  
2089   Give me all, give me all, give me all your att...           True  
...                                                  ...            ...  
57544  What, is this bitch fucking with Z-Ro   Mother...           True  
57545  [Hook - 2x]   Guerilla till I die, mama don't ...           True  
57550  (Chorus - 2x)   Lord tell me why   Ooh child, ...           True  
57560  [Z-Ro]   Since I been out by myself, I keep th...           True  
57561  [Z-Ro]   Houston Texas is my city, Ridgemont 4...           True  

[1356 rows x 4 columns]

In [5]:
#ramdomly extract 4068 rows with explicit_label = False, which is 3 times as many as song_data_1
song_data_0 = song_data.loc[song_data['explicit_label'] == 'False']
song_data_0 = song_data_0.sample(n=4068, replace=False, random_state=100)
song_data_0

artist                         song  \
51337                 Santana          Somewhere In Heaven   
28056           Cliff Richard  Can't Take The Hurt Anymore   
46109  Nitty Gritty Dirt Band          Stand A Little Rain   
19827                      U2                    Dirty Day   
44161                 Misfits            Only Make Believe   
...                       ...                          ...   
17703                 Rihanna             We All Want Love   
48905              Pretenders                   2000 Miles   
22776                  ZZ Top              My Mind Is Gone   
37852           Jimmy Buffett      Beach House On The Moon   
20136              Underworld               Little Speaker   

                                                    text explicit_label  
51337  Somewhere   In heaven   There is a place   Wai...          False  
28056  Now that the past has ended   My life's an ope...          False  
46109  Dark cloud is coming   Headed straight for you...          False  
19827  I don't know you   And you don't know the half...          False  
44161  People see us everywhere   They think you real...          False  
...                                                  ...            ...  
17703  We all, we all, we all, we all, we all   We al...          False  
48905  He's gone two thousand miles   It's very far  ...          False  
22776  No keyboards, just Pearly Gates and a lot of s...          False  
37852  Cameron's getting logical,   A Vulcan in disgu...          False  
20136  Go   Did you get these from round our's   Go  ...          False  

[4068 rows x 4 columns]

In [6]:
song_data = pd.concat([song_data_0,song_data_1], axis = 0)
song_data

artist                         song  \
51337                 Santana          Somewhere In Heaven   
28056           Cliff Richard  Can't Take The Hurt Anymore   
46109  Nitty Gritty Dirt Band          Stand A Little Rain   
19827                      U2                    Dirty Day   
44161                 Misfits            Only Make Believe   
...                       ...                          ...   
57544                    Z-Ro               Gripping Grain   
57545                    Z-Ro          Guerilla Till I Die   
57550                    Z-Ro             Lord Tell Me Why   
57560                    Z-Ro           Talkin' Down On Me   
57561                    Z-Ro              That'z Who I Am   

                                                    text explicit_label  
51337  Somewhere   In heaven   There is a place   Wai...          False  
28056  Now that the past has ended   My life's an ope...          False  
46109  Dark cloud is coming   Headed straight for you...          False  
19827  I don't know you   And you don't know the half...          False  
44161  People see us everywhere   They think you real...          False  
...                                                  ...            ...  
57544  What, is this bitch fucking with Z-Ro   Mother...           True  
57545  [Hook - 2x]   Guerilla till I die, mama don't ...           True  
57550  (Chorus - 2x)   Lord tell me why   Ooh child, ...           True  
57560  [Z-Ro]   Since I been out by myself, I keep th...           True  
57561  [Z-Ro]   Houston Texas is my city, Ridgemont 4...           True  

[5424 rows x 4 columns]

In [7]:
lyrics_data = []
for i in range(len(song_data)):
    text = song_data.iloc[i,2]
    lyrics_data.append(text)

In [8]:
#lyrics_data[0]
#lyrics_data[5423]
#len(lyrics_data)
lyrics_data

["Somewhere   In heaven   There is a place   Waiting for you and me      He made a promise   Gave every drop of Blood   Died on the cross   so we'd be free.      Oh Oh Oh Oh      Somewhere, Somewhere   In Heaven   There's a place   Waiting, waiting for you and me      He made a promise   Gave every drop of Blood   And died on the cross   So we'd be free.      Somewhere, Somewhere   In Heaven   There is a place   Waiting, waiting for you and me      He made a promise   When He gave every drop of His blood   Died on the cross   So we'd be free.  ",
 "Now that the past has ended   My life's an open door   I know that we could have been mended   Oh but I can't take the hurt anymore   Can't take the hurt anymore   Ooh ooh can't take the hurt anymore   The rainbow's over   But I've seen it leave before   A love that's been left in the corner   Ooh 'cause I can't take the hurt anymore   Can't take the hurt anymore   Ooh ooh can't take the hurt anymore   Lady of my lady's   Can't we find the r

In [9]:
lyrics_label = []
for i in range(len(song_data)):
    label = song_data.iloc[i,3]
    if label=="False":
        label = 0
    else:
        label = 1
    lyrics_label.append(label)

In [10]:
#lyrics_label[0]
#lyrics_label[5423]
#len(lyrics_label)
lyrics_label

[0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,


In [11]:
train_data, test_data, train_label, test_label = train_test_split(lyrics_data, lyrics_label, test_size=0.3, random_state=100)

In [12]:
train_data

["Bawitdaba, da bang, da dang diggy diggy, diggy, said the boogie, said up jump the boogie      My name is kid   Kid rock!      Bawitdaba da bang da bang diggy diggy diggy   Shake the boogie said up jump the boogie   Bawitdaba da bang da bang diggy diggy diggy   Shake the boogie said up jump the boogie      Bawitdaba da bang da bang diggy diggy diggy   Shake the boogie said up jump the boogie   Bawitdaba da bang da bang diggy diggy diggy   Shake the boogie said up jump the boogie      And this is for the questions that don't have an answer   The midnight glances   And the topless dancers   The can of freaks      Cars packed with speakers   The g's with the forty's   And the chicks with beepers   The northern lights      And the southern comfort   And it don't even matter if your veins are punctured   All the crackheads, the critics, the cities   And all my heroes at the methodone clinics      All you bastards at the i.r.s.   For the crooked cops and the cluttered desks   For the shots 

In [13]:
train_label

[1,
 1,
 0,
 0,
 0,
 0,
 1,
 0,
 0,
 0,
 0,
 0,
 1,
 0,
 0,
 0,
 0,
 0,
 0,
 1,
 1,
 0,
 0,
 0,
 0,
 0,
 1,
 0,
 0,
 0,
 0,
 0,
 0,
 1,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 1,
 1,
 0,
 0,
 1,
 1,
 0,
 0,
 0,
 1,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 1,
 0,
 1,
 1,
 1,
 0,
 1,
 1,
 1,
 0,
 0,
 1,
 0,
 0,
 0,
 0,
 0,
 0,
 1,
 1,
 1,
 0,
 1,
 0,
 0,
 0,
 1,
 0,
 0,
 1,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 1,
 0,
 1,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 1,
 0,
 0,
 1,
 1,
 0,
 1,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 1,
 0,
 1,
 1,
 0,
 0,
 1,
 1,
 0,
 1,
 0,
 0,
 0,
 1,
 1,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 1,
 0,
 0,
 1,
 1,
 1,
 1,
 0,
 0,
 0,
 0,
 0,
 1,
 0,
 0,
 1,
 1,
 1,
 1,
 0,
 0,
 0,
 0,
 0,
 0,
 1,
 0,
 0,
 1,
 1,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 1,
 1,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 1,
 0,
 0,
 0,
 0,
 1,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 1,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 1,
 0,
 0,
 0,
 0,
 0,
 1,
 0,
 0,
 1,
 0,
 0,
 0,


In [14]:
test_data

["Till I had you I didn't know   That I was missing out   Had to grow up and see the world   Through different shades of doubt   Give me one more chance to dream again   One more chance to feel again   Through your young heart   If only for one day help me try   I wanna see Christmas through your eyes   I want everything to be the way it used to be   Back to being a child again, thinking the world was mine   I wanna see Christmas, Christmas through your eyes   I see the rain, you see the rainbow   Hiding in the clouds   Never afraid to let your love show   Won't you show me how   Wanna learn how to believe again   Find the innocence in me again   Through your young heart   Help me find a way, help me try   I wanna see Christmas through your eyes   I want everything to be the way it used to be   Back to being a child again thinking the world was kind   I wanna see Christmas, Christmas through your eyes   I wanna see Christmas through your eyes   I want everything to be the way it used t

In [15]:
test_label

[0,
 0,
 0,
 0,
 0,
 1,
 0,
 0,
 0,
 1,
 1,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 1,
 1,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 1,
 0,
 1,
 1,
 0,
 0,
 0,
 1,
 0,
 0,
 0,
 1,
 0,
 0,
 0,
 0,
 1,
 0,
 1,
 0,
 0,
 0,
 1,
 0,
 1,
 1,
 0,
 1,
 0,
 0,
 0,
 0,
 0,
 1,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 1,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 1,
 0,
 1,
 0,
 0,
 1,
 0,
 0,
 1,
 0,
 1,
 0,
 0,
 0,
 0,
 1,
 0,
 0,
 1,
 1,
 0,
 1,
 0,
 0,
 1,
 0,
 1,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 1,
 0,
 1,
 1,
 0,
 1,
 0,
 0,
 0,
 0,
 0,
 1,
 0,
 1,
 0,
 1,
 0,
 0,
 0,
 0,
 1,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 1,
 0,
 1,
 0,
 0,
 0,
 1,
 0,
 1,
 0,
 0,
 1,
 0,
 0,
 0,
 0,
 0,
 0,
 1,
 1,
 0,
 1,
 0,
 0,
 0,
 0,
 0,
 1,
 0,
 0,
 1,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 1,
 0,
 0,
 1,
 1,
 0,
 0,
 1,
 0,
 0,
 0,
 0,
 1,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 1,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 1,
 0,
 0,
 1,
 0,
 0,
 1,
 0,
 1,
 0,
 0,
 1,
 0,
 0,
 0,


# Classification Models

In [16]:
vectorizer = CountVectorizer(stop_words = 'english') #TfidfVectorizer()
vectorizer.fit(train_data)
train_vecs = vectorizer.transform(train_data)
test_vecs = vectorizer.transform(test_data)

### Logistic Regression

In [17]:
def classification(vectorizer, model, fit_vect=False):
  if fit_vect:
    vectorizer.fit(train_data)
    
  train_vecs = vectorizer.transform(train_data)
  test_vecs = vectorizer.transform(test_data)
    
  model.fit(train_vecs, train_label)

  train_preds = model.predict(train_vecs)
  train_f1 = f1_score(train_label, train_preds, average='micro')

  test_preds = model.predict(test_vecs)
  test_f1 = f1_score(test_label, test_preds, average='micro')

  cm = confusion_matrix(test_label, test_preds)
  print("Confusion Matrix : \n", cm, " \n")

  report = classification_report(test_label, test_preds)
  print(report)

  return train_f1,test_f1

### Turn parameter

In [18]:
number = list(np.arange(0.1, 1.0, 0.1))
for c in number:
    model = LogisticRegression(C=c)
    print(c)
    classification(vectorizer, model)

0.1


/Users/tanyufei/anaconda3/lib/python3.6/site-packages/sklearn/linear_model/_logistic.py:764: ConvergenceWarning: lbfgs failed to converge (status=1):
STOP: TOTAL NO. of ITERATIONS REACHED LIMIT.

Increase the number of iterations (max_iter) or scale the data as shown in:
    https://scikit-learn.org/stable/modules/preprocessing.html
Please also refer to the documentation for alternative solver options:
    https://scikit-learn.org/stable/modules/linear_model.html#logistic-regression
  extra_warning_msg=_LOGISTIC_SOLVER_CONVERGENCE_MSG)


Confusion Matrix : 
 [[1184   43]
 [ 144  257]]  

              precision    recall  f1-score   support

           0       0.89      0.96      0.93      1227
           1       0.86      0.64      0.73       401

    accuracy                           0.89      1628
   macro avg       0.87      0.80      0.83      1628
weighted avg       0.88      0.89      0.88      1628

0.2


/Users/tanyufei/anaconda3/lib/python3.6/site-packages/sklearn/linear_model/_logistic.py:764: ConvergenceWarning: lbfgs failed to converge (status=1):
STOP: TOTAL NO. of ITERATIONS REACHED LIMIT.

Increase the number of iterations (max_iter) or scale the data as shown in:
    https://scikit-learn.org/stable/modules/preprocessing.html
Please also refer to the documentation for alternative solver options:
    https://scikit-learn.org/stable/modules/linear_model.html#logistic-regression
  extra_warning_msg=_LOGISTIC_SOLVER_CONVERGENCE_MSG)


Confusion Matrix : 
 [[1181   46]
 [ 142  259]]  

              precision    recall  f1-score   support

           0       0.89      0.96      0.93      1227
           1       0.85      0.65      0.73       401

    accuracy                           0.88      1628
   macro avg       0.87      0.80      0.83      1628
weighted avg       0.88      0.88      0.88      1628

0.30000000000000004


...

/Users/tanyufei/anaconda3/lib/python3.6/site-packages/sklearn/linear_model/_logistic.py:764: ConvergenceWarning: lbfgs failed to converge (status=1):
STOP: TOTAL NO. of ITERATIONS REACHED LIMIT.

Increase the number of iterations (max_iter) or scale the data as shown in:
    https://scikit-learn.org/stable/modules/preprocessing.html
Please also refer to the documentation for alternative solver options:
    https://scikit-learn.org/stable/modules/linear_model.html#logistic-regression
  extra_warning_msg=_LOGISTIC_SOLVER_CONVERGENCE_MSG)


Confusion Matrix : 
 [[1168   59]
 [ 137  264]]  

              precision    recall  f1-score   support

           0       0.90      0.95      0.92      1227
           1       0.82      0.66      0.73       401

    accuracy                           0.88      1628
   macro avg       0.86      0.81      0.83      1628
weighted avg       0.88      0.88      0.87      1628

0.8


/Users/tanyufei/anaconda3/lib/python3.6/site-packages/sklearn/linear_model/_logistic.py:764: ConvergenceWarning: lbfgs failed to converge (status=1):
STOP: TOTAL NO. of ITERATIONS REACHED LIMIT.

Increase the number of iterations (max_iter) or scale the data as shown in:
    https://scikit-learn.org/stable/modules/preprocessing.html
Please also refer to the documentation for alternative solver options:
    https://scikit-learn.org/stable/modules/linear_model.html#logistic-regression
  extra_warning_msg=_LOGISTIC_SOLVER_CONVERGENCE_MSG)


Confusion Matrix : 
 [[1168   59]
 [ 136  265]]  

              precision    recall  f1-score   support

           0       0.90      0.95      0.92      1227
           1       0.82      0.66      0.73       401

    accuracy                           0.88      1628
   macro avg       0.86      0.81      0.83      1628
weighted avg       0.88      0.88      0.88      1628

0.9
Confusion Matrix : 
 [[1167   60]
 [ 136  265]]  

              precision    recall  f1-score   support

           0       0.90      0.95      0.92      1227
           1       0.82      0.66      0.73       401

    accuracy                           0.88      1628
   macro avg       0.86      0.81      0.83      1628
weighted avg       0.88      0.88      0.88      1628



/Users/tanyufei/anaconda3/lib/python3.6/site-packages/sklearn/linear_model/_logistic.py:764: ConvergenceWarning: lbfgs failed to converge (status=1):
STOP: TOTAL NO. of ITERATIONS REACHED LIMIT.

Increase the number of iterations (max_iter) or scale the data as shown in:
    https://scikit-learn.org/stable/modules/preprocessing.html
Please also refer to the documentation for alternative solver options:
    https://scikit-learn.org/stable/modules/linear_model.html#logistic-regression
  extra_warning_msg=_LOGISTIC_SOLVER_CONVERGENCE_MSG)


In [19]:
model = LogisticRegression(C=0.1)
classification(vectorizer, model)

Confusion Matrix : 
 [[1184   43]
 [ 144  257]]  

              precision    recall  f1-score   support

           0       0.89      0.96      0.93      1227
           1       0.86      0.64      0.73       401

    accuracy                           0.89      1628
   macro avg       0.87      0.80      0.83      1628
weighted avg       0.88      0.89      0.88      1628



/Users/tanyufei/anaconda3/lib/python3.6/site-packages/sklearn/linear_model/_logistic.py:764: ConvergenceWarning: lbfgs failed to converge (status=1):
STOP: TOTAL NO. of ITERATIONS REACHED LIMIT.

Increase the number of iterations (max_iter) or scale the data as shown in:
    https://scikit-learn.org/stable/modules/preprocessing.html
Please also refer to the documentation for alternative solver options:
    https://scikit-learn.org/stable/modules/linear_model.html#logistic-regression
  extra_warning_msg=_LOGISTIC_SOLVER_CONVERGENCE_MSG)


(0.9847207586933614, 0.8851351351351351)

# Topic Modeling

## LDA

### for explict lyrics

Approach 1

In [20]:
explict_lyrics = song_data_1.text
explict_lyrics

128               I'm sitting in my chair watching the ...
129      I'm a big fuckin' dick   I'm a pain in your as...
909      Singing Radiohead at the top of our lungs   Wi...
929      Let them know that we're still rock n roll   I...
2089     Give me all, give me all, give me all your att...
                               ...                        
57544    What, is this bitch fucking with Z-Ro   Mother...
57545    [Hook - 2x]   Guerilla till I die, mama don't ...
57550    (Chorus - 2x)   Lord tell me why   Ooh child, ...
57560    [Z-Ro]   Since I been out by myself, I keep th...
57561    [Z-Ro]   Houston Texas is my city, Ridgemont 4...
Name: text, Length: 1356, dtype: object

In [21]:
explict_lyrics_list = song_data_1.text.values.tolist()
explict_lyrics_list

["         I'm sitting in my chair watching the TV   It's not even on but there's plenty for me to see   I just lit some crazy ass shit   that my friend overnight mailed to me      I'm fucking wasted   It's the best shit I ever tasted   I think they fucking laced it   Cause I'm so damn lambasted      Oh my friend came over so I packed him a pipe   I told him he better go easy with this shit but he didn't believe the hype   He sparked three bows just to show he could take it   Two minutes later he was playing backgammon naked      He's fucking wasted   It's the best shit he ever tasted   He's lost in fucking spaced-ed   Cause he's so wicked wicked wasted      Oh I spent the last two hours   hiding under my bed   Cause I looked in the garbage can   and I think I saw my Uncle Louie's head      I'm fucking wasted      Well my friend blew a hit into my pet bird's face   The bird laughed hysterically and started to moonwalk all over the place   He tripped over the toaster wire and fell on hi

In [22]:
lda_tfidf = TfidfVectorizer(stop_words = 'english')
explict_lyrics_vecs = lda_tfidf.fit_transform(explict_lyrics_list)

In [26]:
lda = LatentDirichletAllocation(n_components = 5, random_state = 100)
lda.fit(explict_lyrics_vecs)

LatentDirichletAllocation(n_components=5, random_state=100)

In [27]:
for index, topic in enumerate(lda.components_):
    print(f'Top 15 words for Topic # {index}')
    print([lda_tfidf.get_feature_names()[i] for i in topic.argsort()[-15:]])
    print('\n')

Top 15 words for Topic # 0
['pon', 'carnival', 'diggy', 'angelfuck', 'patna', 'woogie', 'turkee', 'carnage', 'tek', 'nuh', 'seh', 'gal', 'mi', 'di', 'yuh']


Top 15 words for Topic # 1
['ruca', 'aura', 'twilight', 'cigaro', 'calmer', 'gwaan', 'evolution', 'canned', 'winkle', 'nying', 'birdy', 'hellion', 'ramona', 'phresh', 'starfuckers']


Top 15 words for Topic # 2
['wasteland', 'ringmaster', 'nicole', 'garment', 'steals', 'hem', 'hypocrites', 'superficial', 'hott', 'purpose', 'bicken', 'gunn', 'tormentor', 'brazy', 'fikir']


Top 15 words for Topic # 3
['shit', 'ain', 'cause', 'nigga', 'want', 'll', 'fuck', 'yeah', 'love', 'oh', 'just', 'know', 'got', 'don', 'like']


Top 15 words for Topic # 4
['jugglin', 'hahn', 'lizard', 'perverts', 'juggalas', 'hanh', 'hannah', 'apocalypse', 'peacock', 'ion', 'widowmaker', 'ebin', 'superstitious', 'sikamikanico', 'demonomania']




In [28]:
print(lda.components_)

[[0.20005162 0.20002057 0.20003855 ... 0.20003619 0.20004542 0.20003115]
 [0.20005179 0.20002062 0.20003868 ... 0.20003631 0.20317633 0.20003122]
 [0.20005193 0.20002067 0.20003878 ... 0.20003641 0.20004616 0.20003131]
 [0.30763584 0.47020678 0.26726226 ... 0.24677513 0.38376316 0.289582  ]
 [0.2000519  0.20002066 0.20003876 ... 0.20003639 0.20004561 0.20003129]]


Approach 2

In [29]:
len(STOPWORDS)
stopwords = set(STOPWORDS)
stopwords.update(["yeah", "oh", "ya", "let"])
len(stopwords)

341

In [30]:
def lemmatization(text):
    wnl = WordNetLemmatizer()
    lemmatization = wnl.lemmatize(text, pos='n')
    return lemmatization

In [31]:
def lemmatization_stemming(text):
    wnl = WordNetLemmatizer()
    lemmatization = wnl.lemmatize(text, pos='n')
    
    stemmer = PorterStemmer()
    stemming = stemmer.stem(lemmatization)
    return stemming

In [32]:
#token = simple_preprocess(explict_lyrics_data[0])
#token

In [33]:
def text_preprocess(text):
    result = []
    for token in simple_preprocess(text):
        if token not in stopwords and len(token) > 3:
            result.append(lemmatization_stemming(token))
    return result

In [34]:
processed_lyrics = song_data_1['text'].map(text_preprocess)
processed_lyrics

128      [sit, chair, watch, plenti, crazi, shit, frien...
129      [fuckin, dick, pain, drink, beer, slice, charl...
909      [sing, radiohead, lung, boom, blare, fall, lov...
929      [know, rock, roll, care, makeup, like, better,...
2089     [attent, babi, tell, littl, wonder, flawless, ...
                               ...                        
57544    [bitch, fuck, motherfuck, citi, bitch, know, h...
57545    [hook, guerilla, till, mama, come, blast, guer...
57550    [choru, lord, tell, child, thing, gonna, easie...
57560    [bitch, nina, enemi, want, nigga, seen, hater,...
57561    [houston, texa, citi, ridgemont, block, trust,...
Name: text, Length: 1356, dtype: object

In [35]:
dictionary = Dictionary(processed_lyrics)
dictionary.filter_extremes()

In [36]:
#len(dictionary)
#print(dictionary)

In [37]:
bow_corpus = [dictionary.doc2bow(doc) for doc in processed_lyrics]
#bow_corpus

In [38]:
tfidf_model = TfidfModel(bow_corpus)
tfidf_corpus = tfidf_model[bow_corpus]

In [39]:
# bag of words lda model
lda_model = LdaMulticore(bow_corpus, num_topics=5, id2word=dictionary, workers=2)
for idx, topic in lda_model.print_topics(-1):
    print('Topic: {} \nWords: {}'.format(idx, topic))

Topic: 0 
Words: 0.014*"time" + 0.013*"want" + 0.011*"love" + 0.011*"need" + 0.010*"come" + 0.009*"feel" + 0.008*"shit" + 0.008*"tell" + 0.008*"everybodi" + 0.007*"wanna"
Topic: 1 
Words: 0.016*"girl" + 0.012*"come" + 0.010*"feel" + 0.010*"time" + 0.010*"babi" + 0.010*"shit" + 0.009*"right" + 0.008*"nigga" + 0.008*"life" + 0.007*"wanna"
Topic: 2 
Words: 0.029*"nigga" + 0.013*"bitch" + 0.013*"shit" + 0.012*"want" + 0.009*"come" + 0.009*"tell" + 0.007*"choru" + 0.007*"money" + 0.007*"feel" + 0.007*"right"
Topic: 3 
Words: 0.032*"love" + 0.012*"babi" + 0.011*"bitch" + 0.010*"want" + 0.010*"nigga" + 0.010*"girl" + 0.007*"come" + 0.007*"choru" + 0.007*"gotta" + 0.007*"time"
Topic: 4 
Words: 0.014*"want" + 0.013*"come" + 0.011*"nigga" + 0.011*"bitch" + 0.010*"love" + 0.010*"shit" + 0.009*"littl" + 0.009*"right" + 0.008*"choru" + 0.007*"time"


In [40]:
# tfidf lda model num_topics=5
lda_model2 = LdaMulticore(tfidf_corpus, num_topics=5, id2word=dictionary, workers=2)
for idx, topic in lda_model2.print_topics(-1):
    print('Topic: {} \nWords: {}'.format(idx, topic))

Topic: 0 
Words: 0.003*"nigga" + 0.003*"want" + 0.003*"love" + 0.003*"feel" + 0.003*"choru" + 0.002*"wanna" + 0.002*"bitch" + 0.002*"live" + 0.002*"shit" + 0.002*"come"
Topic: 1 
Words: 0.005*"nigga" + 0.003*"choru" + 0.003*"girl" + 0.003*"babi" + 0.003*"love" + 0.002*"gotta" + 0.002*"need" + 0.002*"feel" + 0.002*"shit" + 0.002*"want"
Topic: 2 
Words: 0.006*"nigga" + 0.003*"girl" + 0.003*"love" + 0.003*"bitch" + 0.003*"money" + 0.003*"want" + 0.003*"shit" + 0.002*"right" + 0.002*"feel" + 0.002*"time"
Topic: 3 
Words: 0.004*"love" + 0.003*"hate" + 0.003*"babi" + 0.003*"nigga" + 0.002*"want" + 0.002*"feel" + 0.002*"choru" + 0.002*"come" + 0.002*"money" + 0.002*"bitch"
Topic: 4 
Words: 0.004*"nigga" + 0.003*"love" + 0.003*"bitch" + 0.003*"babi" + 0.003*"shit" + 0.003*"want" + 0.003*"choru" + 0.002*"good" + 0.002*"thing" + 0.002*"girl"


In [41]:
pyLDAvis.enable_notebook()
id2word = dictionary
vis = pyLDAvis.gensim.prepare(lda_model2, tfidf_corpus, id2word)
vis

/Users/tanyufei/anaconda3/lib/python3.6/site-packages/pyLDAvis/_prepare.py:257: FutureWarning: Sorting because non-concatenation axis is not aligned. A future version
of pandas will change to not sort by default.

To accept the future behavior, pass 'sort=False'.

To retain the current behavior and silence the warning, pass 'sort=True'.

  return pd.concat([default_term_info] + list(topic_dfs))


PreparedData(topic_coordinates=              x         y  topics  cluster       Freq
topic                                                
0      0.003440 -0.002181       1        1  25.530567
4      0.013562 -0.006679       2        1  24.779409
2      0.001088 -0.014123       3        1  23.271442
3      0.005690  0.022395       4        1  14.747304
1     -0.023781  0.000588       5        1  11.671270, topic_info=     Category       Freq   Term      Total  loglift  logprob
386   Default  33.000000  nigga  33.000000  30.0000  30.0000
144   Default   4.000000   whoa   4.000000  29.0000  29.0000
464   Default   5.000000  music   5.000000  28.0000  28.0000
448   Default  12.000000   hate  12.000000  27.0000  27.0000
2747  Default   2.000000  shall   2.000000  26.0000  26.0000
...       ...        ...    ...        ...      ...      ...
62     Topic5   1.643855   away  13.839158   0.0176  -6.3687
123    Topic5   1.678024  gonna  15.853450  -0.0977  -6.3481
166    Topic5   1.727238   come  17.747793  -0.1817  -6.3192
378    Topic5   1.601879   life  16.327229  -0.1736  -6.3946
337    Topic5   1.527941  money  16.407904  -0.2258  -6.4418

[395 rows x 6 columns], token_table=      Topic      Freq         Term
term                              
713       2  0.356135        admit
713       5  0.356135        admit
2581      5  0.583954        alley
3340      1  0.842791         anti
3081      5  0.657885    apocalyps
...     ...       ...          ...
111       5  0.126461        wrong
2770      1  0.488278        yeezi
3363      2  0.638114     yelawolf
3259      2  0.709977  youngbloodz
2171      4  0.571195        youth

[745 rows x 3 columns], R=30, lambda_step=0.01, plot_opts={'xlab': 'PC1', 'ylab': 'PC2'}, topic_order=[1, 5, 3, 4, 2])

Approach 3

In [66]:
lda_model3 = gensim.models.ldamodel.LdaModel(tfidf_corpus, num_topics=2, id2word=dictionary)
for idx, topic in lda_model3.print_topics(-1):
    print('Topic: {} \nWords: {}'.format(idx, topic))

Topic: 0 
Words: 0.003*"nigga" + 0.003*"babi" + 0.003*"want" + 0.003*"love" + 0.003*"time" + 0.003*"bitch" + 0.003*"choru" + 0.002*"girl" + 0.002*"come" + 0.002*"gonna"
Topic: 1 
Words: 0.005*"nigga" + 0.003*"love" + 0.003*"shit" + 0.003*"feel" + 0.003*"choru" + 0.003*"girl" + 0.002*"bitch" + 0.002*"wanna" + 0.002*"need" + 0.002*"life"


In [67]:
pyLDAvis.enable_notebook()
id2word = dictionary
vis = pyLDAvis.gensim.prepare(lda_model3, tfidf_corpus, id2word)
vis

/Users/tanyufei/anaconda3/lib/python3.6/site-packages/pyLDAvis/_prepare.py:257: FutureWarning: Sorting because non-concatenation axis is not aligned. A future version
of pandas will change to not sort by default.

To accept the future behavior, pass 'sort=False'.

To retain the current behavior and silence the warning, pass 'sort=True'.

  return pd.concat([default_term_info] + list(topic_dfs))


PreparedData(topic_coordinates=             x    y  topics  cluster       Freq
topic                                          
1      0.00494  0.0       1        1  56.712975
0     -0.00494  0.0       2        1  43.287022, topic_info=     Category       Freq   Term      Total  loglift  logprob
164   Default  18.000000   babi  18.000000  30.0000  30.0000
161   Default  16.000000   time  16.000000  29.0000  29.0000
1176  Default   7.000000  blood   7.000000  28.0000  28.0000
461   Default  10.000000   gone  10.000000  27.0000  27.0000
225   Default  11.000000   mind  11.000000  26.0000  26.0000
...       ...        ...    ...        ...      ...      ...
378    Topic2   5.980632   life  16.355228  -0.1687  -6.3880
392    Topic2   5.332702   real  11.770330   0.0456  -6.5026
200    Topic2   5.848671   feel  19.485109  -0.3661  -6.4103
42     Topic2   5.659562   shit  19.404667  -0.3948  -6.4431
106    Topic2   5.501668   tell  15.323042  -0.1870  -6.4714

[177 rows x 6 columns], token_table=      Topic      Freq    Term
term                         
791       1  0.730972    aliv
791       2  0.365486    aliv
2581      1  0.517488   alley
2581      2  0.517488   alley
3356      1  0.658798  appeal
...     ...       ...     ...
183       2  0.545248  wonder
318       1  0.494868   world
318       2  0.494868   world
146       1  0.671212   young
146       2  0.335606   young

[252 rows x 3 columns], R=30, lambda_step=0.01, plot_opts={'xlab': 'PC1', 'ylab': 'PC2'}, topic_order=[2, 1])

#### Remove dirty words

In [44]:
file = open('abbo.txt','r')
file = list(file)
bad_words = []
for w in file:
    bad_words.append(re.sub(r'\n','',w))
bad_words

['abbo',
 'abo',
 'abortion',
 'abuse',
 'addict',
 'addicts',
 'adult',
 'africa',
 'african',
 'alla',
 'allah',
 'alligatorbait',
 'amateur',
 'american',
 'anal',
 'analannie',
 'analsex',
 'angie',
 'angry',
 'anus',
 'arab',
 'arabs',
 'areola',
 'argie',
 'aroused',
 'arse',
 'arsehole',
 'asian',
 'ass',
 'assassin',
 'assassinate',
 'assassination',
 'assault',
 'assbagger',
 'assblaster',
 'assclown',
 'asscowboy',
 'asses',
 'assfuck',
 'assfucker',
 'asshat',
 'asshole',
 'assholes',
 'asshore',
 'assjockey',
 'asskiss',
 'asskisser',
 'assklown',
 'asslick',
 'asslicker',
 'asslover',
 'assman',
 'assmonkey',
 'assmunch',
 'assmuncher',
 'asspacker',
 'asspirate',
 'asspuppies',
 'assranger',
 'asswhore',
 'asswipe',
 'athletesfoot',
 'attack',
 'australian',
 'babe',
 'babies',
 'backdoor',
 'backdoorman',
 'backseat',
 'badfuck',
 'balllicker',
 'balls',
 'ballsack',
 'banging',
 'baptist',
 'barelylegal',
 'barf',
 'barface',
 'barfface',
 'bast',
 'bastard ',
 'bazonga

In [49]:
stopwords = set(STOPWORDS)
stopwords.update(bad_words)
stopwords.update(["yeah","oh", "ya", "let"])
len(stopwords)

1723

In [50]:
def text_preprocess(text):
    result = []
    for token in simple_preprocess(text):
        if token not in stopwords and len(token) > 3:
            result.append(lemmatization_stemming(token))
    return result

In [51]:
processedlyrics = song_data_1['text'].map(text_preprocess)

Ddictionary = Dictionary(processedlyrics)
Ddictionary.filter_extremes()

Bow_corpus = [Ddictionary.doc2bow(doc) for doc in processedlyrics]

Tfidf_model = TfidfModel(Bow_corpus)
Tfidf_corpus = Tfidf_model[Bow_corpus]

In [53]:
lda_model4 = gensim.models.ldamodel.LdaModel(Tfidf_corpus, num_topics=5, id2word=Ddictionary)
for idx, topic in lda_model4.print_topics(-1):
    print('Topic: {} \nWords: {}'.format(idx, topic))

Topic: 0 
Words: 0.003*"love" + 0.003*"babi" + 0.003*"wanna" + 0.003*"nigga" + 0.002*"feel" + 0.002*"wait" + 0.002*"gonna" + 0.002*"need" + 0.002*"tell" + 0.002*"choru"
Topic: 1 
Words: 0.003*"love" + 0.003*"want" + 0.003*"choru" + 0.003*"girl" + 0.003*"babi" + 0.003*"life" + 0.003*"said" + 0.003*"tonight" + 0.003*"feel" + 0.003*"come"
Topic: 2 
Words: 0.004*"love" + 0.004*"money" + 0.003*"choru" + 0.003*"want" + 0.003*"time" + 0.002*"right" + 0.002*"think" + 0.002*"come" + 0.002*"nigga" + 0.002*"life"
Topic: 3 
Words: 0.004*"feel" + 0.003*"girl" + 0.003*"love" + 0.003*"choru" + 0.003*"come" + 0.003*"want" + 0.003*"time" + 0.003*"hate" + 0.002*"night" + 0.002*"think"
Topic: 4 
Words: 0.003*"want" + 0.003*"right" + 0.003*"need" + 0.002*"nigga" + 0.002*"love" + 0.002*"choru" + 0.002*"babi" + 0.002*"feel" + 0.002*"look" + 0.002*"wanna"


### for normal lyrics

In [54]:
stopwords = set(STOPWORDS)
#stopwords.update(bad_words)
stopwords.update(["yeah","oh", "ya", "let"])
len(stopwords)

341

In [55]:
def text_preprocess(text):
    result = []
    for token in simple_preprocess(text):
        if token not in stopwords and len(token) > 3:
            result.append(lemmatization_stemming(token))
    return result

In [59]:
processed_normal_lyrics = song_data_0['text'].map(text_preprocess)

normal_dictionary = Dictionary(processed_normal_lyrics)
normal_dictionary.filter_extremes()

bow_corpus_normal = [normal_dictionary.doc2bow(doc) for doc in processed_normal_lyrics]

tfidf_model_normal = TfidfModel(bow_corpus_normal)
tfidf_corpus_normal = tfidf_model_normal[bow_corpus_normal]

lda_model_normal = gensim.models.ldamodel.LdaModel(tfidf_corpus_normal, num_topics=10, id2word=normal_dictionary)

for idx, topic in lda_model_normal.print_topics(-1):
    print('Topic: {} \nWords: {}'.format(idx, topic))

Topic: 0 
Words: 0.024*"weigh" + 0.020*"cat" + 0.013*"cowboy" + 0.011*"coin" + 0.009*"melodi" + 0.009*"fountain" + 0.009*"arrow" + 0.009*"lost" + 0.008*"eager" + 0.008*"corpor"
Topic: 1 
Words: 0.014*"abl" + 0.013*"round" + 0.011*"song" + 0.011*"spread" + 0.009*"puso" + 0.009*"wala" + 0.008*"crazi" + 0.008*"sunshin" + 0.007*"till" + 0.007*"built"
Topic: 2 
Words: 0.015*"admit" + 0.008*"physic" + 0.008*"throat" + 0.007*"cure" + 0.006*"frozen" + 0.006*"discov" + 0.006*"hymn" + 0.006*"wreck" + 0.006*"cool" + 0.005*"babi"
Topic: 3 
Words: 0.025*"awhil" + 0.018*"harder" + 0.015*"occup" + 0.014*"snow" + 0.012*"vocal" + 0.011*"sing" + 0.010*"colder" + 0.009*"row" + 0.009*"good" + 0.008*"honest"
Topic: 4 
Words: 0.016*"want" + 0.011*"love" + 0.010*"lift" + 0.010*"wrong" + 0.009*"bitter" + 0.009*"high" + 0.009*"mighti" + 0.009*"celebr" + 0.008*"aliv" + 0.008*"come"
Topic: 5 
Words: 0.007*"feel" + 0.006*"love" + 0.005*"safe" + 0.005*"tonight" + 0.005*"gone" + 0.005*"like" + 0.005*"littl" + 0.005

In [61]:
pyLDAvis.enable_notebook()
id2word = normal_dictionary
vis = pyLDAvis.gensim.prepare(lda_model_normal, tfidf_corpus_normal, id2word)
vis

/Users/tanyufei/anaconda3/lib/python3.6/site-packages/pyLDAvis/_prepare.py:257: FutureWarning: Sorting because non-concatenation axis is not aligned. A future version
of pandas will change to not sort by default.

To accept the future behavior, pass 'sort=False'.

To retain the current behavior and silence the warning, pass 'sort=True'.

  return pd.concat([default_term_info] + list(topic_dfs))


PreparedData(topic_coordinates=              x         y  topics  cluster       Freq
topic                                                
5      0.108779 -0.000890       1        1  45.360455
4      0.103490 -0.059110       2        1  12.230032
1      0.043845  0.126027       3        1   9.296304
6      0.000881 -0.009793       4        1   7.243501
7      0.005951 -0.055647       5        1   7.081054
8     -0.020573  0.020161       6        1   5.060139
3     -0.062729 -0.027100       7        1   3.764114
9     -0.068446 -0.015572       8        1   3.623788
2     -0.026307  0.009190       9        1   3.416451
0     -0.084891  0.012734      10        1   2.924161, topic_info=     Category       Freq   Term       Total  loglift  logprob
1370  Default  22.000000  awhil   22.000000  30.0000  30.0000
1524  Default  23.000000   lisa   23.000000  29.0000  29.0000
3208  Default  16.000000   eddi   16.000000  28.0000  28.0000
28    Default  50.000000   lost   50.000000  27.0000  27.0000
256   Default  25.000000    abl   25.000000  26.0000  26.0000
...       ...        ...    ...         ...      ...      ...
954   Topic10   1.586985  haven   16.266356   1.2049  -5.8555
445   Topic10   1.711768  wanna   37.848930   0.4361  -5.7798
29    Topic10   1.776814   love  122.042664  -0.6974  -5.7425
114   Topic10   1.669128  dream   62.236656  -0.0865  -5.8051
22    Topic10   1.588908   know   67.150154  -0.2117  -5.8543

[558 rows x 6 columns], token_table=      Topic      Freq    Term
term                         
256       3  0.948189     abl
2384      1  0.896959   accid
1840      1  0.126796     act
1840      2  0.760776     act
1362      3  0.886135  actual
...     ...       ...     ...
232       4  0.022595    year
232       5  0.158167    year
232       6  0.022595    year
232       8  0.067786    year
2826      7  0.917976   zappa

[1376 rows x 3 columns], R=30, lambda_step=0.01, plot_opts={'xlab': 'PC1', 'ylab': 'PC2'}, topic_order=[6, 5, 2, 7, 8, 9, 4, 10, 3, 1])

In [62]:
lda_model_normal2 = gensim.models.ldamodel.LdaModel(tfidf_corpus_normal, num_topics=8, id2word=normal_dictionary)

for idx, topic in lda_model_normal2.print_topics(-1):
    print('Topic: {} \nWords: {}'.format(idx, topic))

Topic: 0 
Words: 0.009*"love" + 0.008*"want" + 0.007*"feel" + 0.007*"tonight" + 0.006*"thousand" + 0.005*"tomorrow" + 0.005*"bitter" + 0.005*"lisa" + 0.005*"mighti" + 0.005*"come"
Topic: 1 
Words: 0.011*"wanna" + 0.010*"occup" + 0.008*"seventi" + 0.007*"glorifi" + 0.007*"good" + 0.007*"love" + 0.007*"coin" + 0.006*"babi" + 0.006*"mule" + 0.006*"fountain"
Topic: 2 
Words: 0.017*"eddi" + 0.014*"cat" + 0.007*"aliv" + 0.005*"disintegr" + 0.005*"circumst" + 0.005*"think" + 0.005*"disco" + 0.005*"purpl" + 0.004*"depart" + 0.004*"destruct"
Topic: 3 
Words: 0.010*"bell" + 0.009*"lucki" + 0.008*"want" + 0.008*"born" + 0.008*"ring" + 0.008*"mama" + 0.007*"hallelujah" + 0.007*"ladi" + 0.007*"mother" + 0.006*"ooooh"
Topic: 4 
Words: 0.011*"fortress" + 0.008*"built" + 0.008*"tearin" + 0.007*"love" + 0.006*"darkest" + 0.005*"bald" + 0.005*"gonna" + 0.005*"bright" + 0.005*"chain" + 0.004*"caus"
Topic: 5 
Words: 0.007*"lost" + 0.006*"travelin" + 0.006*"walk" + 0.006*"morn" + 0.006*"aliv" + 0.006*"peop

In [63]:
pyLDAvis.enable_notebook()
id2word = normal_dictionary
vis = pyLDAvis.gensim.prepare(lda_model_normal2, tfidf_corpus_normal, id2word)
vis

/Users/tanyufei/anaconda3/lib/python3.6/site-packages/pyLDAvis/_prepare.py:257: FutureWarning: Sorting because non-concatenation axis is not aligned. A future version
of pandas will change to not sort by default.

To accept the future behavior, pass 'sort=False'.

To retain the current behavior and silence the warning, pass 'sort=True'.

  return pd.concat([default_term_info] + list(topic_dfs))


PreparedData(topic_coordinates=              x         y  topics  cluster       Freq
topic                                                
0      0.118128 -0.044105       1        1  33.492405
5      0.032959  0.131863       2        1  15.735771
3      0.051820 -0.044923       3        1  14.738615
4      0.001322  0.022531       4        1  14.633003
1     -0.031868 -0.025972       5        1   6.416291
2     -0.035280 -0.005399       6        1   6.099889
6     -0.051616 -0.022497       7        1   5.323267
7     -0.085463 -0.011498       8        1   3.560758, topic_info=     Category       Freq      Term       Total  loglift  logprob
256   Default  22.000000       abl   22.000000  30.0000  30.0000
3208  Default  20.000000      eddi   20.000000  29.0000  29.0000
1461  Default  30.000000  fortress   30.000000  28.0000  28.0000
2594  Default  15.000000    harder   15.000000  27.0000  27.0000
2306  Default  17.000000       cat   17.000000  26.0000  26.0000
...       ...        ...       ...         ...      ...      ...
111    Topic8   1.933909    believ   36.935268   0.3856  -5.8548
27     Topic8   1.920219     light   35.951614   0.4055  -5.8619
42     Topic8   1.980681      babi   53.229286   0.0440  -5.8309
52     Topic8   1.812249     gonna   54.160187  -0.0622  -5.9198
29     Topic8   1.975834      love  123.293427  -0.7984  -5.8333

[484 rows x 6 columns], token_table=      Topic      Freq   Term
term                        
256       5  0.089410    abl
256       8  0.849397    abl
2384      1  0.961432  accid
1840      1  0.106777    act
1840      3  0.106777    act
...     ...       ...    ...
232       5  0.024505   year
232       6  0.024505   year
232       7  0.049011   year
1278      8  0.344966   york
2826      4  0.800343  zappa

[1165 rows x 3 columns], R=30, lambda_step=0.01, plot_opts={'xlab': 'PC1', 'ylab': 'PC2'}, topic_order=[1, 6, 4, 5, 2, 3, 7, 8])

In [64]:
lda_model_normal3 = gensim.models.ldamodel.LdaModel(tfidf_corpus_normal, num_topics=6, id2word=normal_dictionary)

for idx, topic in lda_model_normal3.print_topics(-1):
    print('Topic: {} \nWords: {}'.format(idx, topic))

Topic: 0 
Words: 0.009*"awhil" + 0.008*"lucki" + 0.008*"good" + 0.007*"distanc" + 0.007*"hallelujah" + 0.007*"ride" + 0.006*"love" + 0.006*"sing" + 0.006*"ladi" + 0.006*"lost"
Topic: 1 
Words: 0.011*"bell" + 0.008*"sacr" + 0.008*"ring" + 0.008*"cowboy" + 0.007*"darkest" + 0.007*"wonder" + 0.005*"bald" + 0.005*"year" + 0.005*"time" + 0.004*"land"
Topic: 2 
Words: 0.016*"bitter" + 0.015*"puso" + 0.007*"dri" + 0.006*"hush" + 0.006*"landscap" + 0.004*"carol" + 0.003*"darl" + 0.003*"come" + 0.003*"love" + 0.003*"poverti"
Topic: 3 
Words: 0.012*"want" + 0.011*"abl" + 0.010*"lisa" + 0.007*"cure" + 0.006*"wala" + 0.005*"laugh" + 0.005*"choru" + 0.005*"feel" + 0.005*"warm" + 0.005*"caus"
Topic: 4 
Words: 0.009*"love" + 0.006*"feel" + 0.006*"tonight" + 0.005*"like" + 0.005*"come" + 0.005*"world" + 0.005*"life" + 0.005*"littl" + 0.004*"away" + 0.004*"think"
Topic: 5 
Words: 0.009*"weigh" + 0.008*"travelin" + 0.007*"mann" + 0.007*"built" + 0.007*"walk" + 0.006*"style" + 0.006*"harder" + 0.006*"rid

In [65]:
pyLDAvis.enable_notebook()
id2word = normal_dictionary
vis = pyLDAvis.gensim.prepare(lda_model_normal3, tfidf_corpus_normal, id2word)
vis

/Users/tanyufei/anaconda3/lib/python3.6/site-packages/pyLDAvis/_prepare.py:257: FutureWarning: Sorting because non-concatenation axis is not aligned. A future version
of pandas will change to not sort by default.

To accept the future behavior, pass 'sort=False'.

To retain the current behavior and silence the warning, pass 'sort=True'.

  return pd.concat([default_term_info] + list(topic_dfs))


PreparedData(topic_coordinates=              x         y  topics  cluster       Freq
topic                                                
4     -0.111632 -0.026537       1        1  43.050987
3      0.009783  0.026398       2        1  14.739670
0      0.006795  0.094848       3        1  14.057170
5      0.044028 -0.061906       4        1  10.969709
1      0.009065 -0.007203       5        1  10.694584
2      0.041961 -0.025600       6        1   6.487875, topic_info=     Category       Freq    Term      Total  loglift  logprob
360   Default  33.000000  bitter  33.000000  30.0000  30.0000
256   Default  31.000000     abl  31.000000  29.0000  29.0000
1524  Default  29.000000    lisa  29.000000  28.0000  28.0000
2996  Default  19.000000    puso  19.000000  27.0000  27.0000
1370  Default  25.000000   awhil  25.000000  26.0000  26.0000
...       ...        ...     ...        ...      ...      ...
91     Topic6   2.564141    like  74.610359  -0.6354  -6.1727
78     Topic6   2.058414     day  21.447214   0.3916  -6.3924
92     Topic6   2.239433    look  48.347389  -0.3370  -6.3081
136    Topic6   2.210029   night  57.323997  -0.5205  -6.3213
131    Topic6   2.268964    feel  83.545753  -0.8708  -6.2950

[390 rows x 6 columns], token_table=      Topic      Freq     Term
term                          
256       2  0.971666      abl
2384      1  0.926789    accid
706       1  0.919584    admit
706       5  0.061306    admit
888       6  0.762899    agoni
...     ...       ...      ...
296       4  0.280953    young
296       5  0.093651    young
296       6  0.187302    young
1329      1  0.949883  younger
2826      4  0.945807    zappa

[926 rows x 3 columns], R=30, lambda_step=0.01, plot_opts={'xlab': 'PC1', 'ylab': 'PC2'}, topic_order=[5, 4, 1, 6, 2, 3])

In [73]:
lda_model_normal4 = gensim.models.ldamodel.LdaModel(tfidf_corpus_normal, num_topics=4, id2word=normal_dictionary)

for idx, topic in lda_model_normal4.print_topics(-1):
    print('Topic: {} \nWords: {}'.format(idx, topic))

Topic: 0 
Words: 0.008*"love" + 0.006*"want" + 0.006*"come" + 0.005*"feel" + 0.005*"tonight" + 0.005*"good" + 0.005*"caus" + 0.005*"walk" + 0.005*"wrong" + 0.004*"life"
Topic: 1 
Words: 0.006*"want" + 0.006*"love" + 0.006*"bitter" + 0.005*"burn" + 0.005*"fool" + 0.005*"gone" + 0.005*"bell" + 0.005*"lucki" + 0.005*"know" + 0.005*"away"
Topic: 2 
Words: 0.008*"abl" + 0.007*"mari" + 0.006*"puso" + 0.006*"choru" + 0.006*"wala" + 0.005*"safe" + 0.005*"cure" + 0.004*"love" + 0.004*"alright" + 0.004*"better"
Topic: 3 
Words: 0.010*"lisa" + 0.010*"lost" + 0.009*"mighti" + 0.008*"spread" + 0.007*"hallelujah" + 0.007*"peopl" + 0.007*"round" + 0.006*"littl" + 0.006*"ooooh" + 0.005*"life"


In [69]:
pyLDAvis.enable_notebook()
id2word = normal_dictionary
vis = pyLDAvis.gensim.prepare(lda_model_normal4, tfidf_corpus_normal, id2word)
vis

/Users/tanyufei/anaconda3/lib/python3.6/site-packages/pyLDAvis/_prepare.py:257: FutureWarning: Sorting because non-concatenation axis is not aligned. A future version
of pandas will change to not sort by default.

To accept the future behavior, pass 'sort=False'.

To retain the current behavior and silence the warning, pass 'sort=True'.

  return pd.concat([default_term_info] + list(topic_dfs))


PreparedData(topic_coordinates=              x         y  topics  cluster       Freq
topic                                                
1      0.085940 -0.010609       1        1  46.657944
3     -0.007527  0.025229       2        1  20.504515
0     -0.043369 -0.070772       3        1  17.701473
2     -0.035043  0.056152       4        1  15.136070, topic_info=     Category       Freq        Term      Total  loglift  logprob
1524  Default  26.000000        lisa  26.000000  30.0000  30.0000
813   Default  24.000000  hallelujah  24.000000  29.0000  29.0000
1370  Default  30.000000       awhil  30.000000  28.0000  28.0000
1461  Default  24.000000    fortress  24.000000  27.0000  27.0000
1731  Default  21.000000    travelin  21.000000  26.0000  26.0000
...       ...        ...         ...        ...      ...      ...
93     Topic4   8.795431        need  57.836502   0.0047  -5.7872
131    Topic4   8.954413        feel  80.720650  -0.3108  -5.7693
22     Topic4   8.338309        know  65.571190  -0.1742  -5.8406
186    Topic4   7.530854        mind  41.178787   0.1892  -5.9424
73     Topic4   7.576299        want  98.277115  -0.6747  -5.9364

[279 rows x 6 columns], token_table=      Topic      Freq   Term
term                        
256       1  0.948719    abl
256       4  0.029647    abl
2384      1  0.148750  accid
2384      3  0.743752  accid
1840      1  0.112183    act
...     ...       ...    ...
952       1  0.738739  wrong
952       2  0.152093  wrong
952       3  0.065183  wrong
952       4  0.065183  wrong
3070      4  0.773692   yang

[605 rows x 3 columns], R=30, lambda_step=0.01, plot_opts={'xlab': 'PC1', 'ylab': 'PC2'}, topic_order=[2, 4, 1, 3])

In [78]:
lda_model_normal5 = gensim.models.ldamodel.LdaModel(tfidf_corpus_normal, num_topics=2, id2word=normal_dictionary)

for idx, topic in lda_model_normal5.print_topics(-1):
    print('Topic: {} \nWords: {}'.format(idx, topic))

Topic: 0 
Words: 0.008*"love" + 0.007*"want" + 0.005*"tonight" + 0.005*"feel" + 0.004*"think" + 0.004*"good" + 0.004*"come" + 0.004*"choru" + 0.004*"ride" + 0.004*"like"
Topic: 1 
Words: 0.005*"love" + 0.005*"world" + 0.004*"know" + 0.004*"gone" + 0.004*"feel" + 0.004*"like" + 0.004*"life" + 0.004*"want" + 0.004*"littl" + 0.004*"come"


In [80]:
pyLDAvis.enable_notebook()
id2word = normal_dictionary
vis = pyLDAvis.gensim.prepare(lda_model_normal5, tfidf_corpus_normal, id2word)
vis

/Users/tanyufei/anaconda3/lib/python3.6/site-packages/pyLDAvis/_prepare.py:257: FutureWarning: Sorting because non-concatenation axis is not aligned. A future version
of pandas will change to not sort by default.

To accept the future behavior, pass 'sort=False'.

To retain the current behavior and silence the warning, pass 'sort=True'.

  return pd.concat([default_term_info] + list(topic_dfs))


PreparedData(topic_coordinates=              x    y  topics  cluster       Freq
topic                                           
1      0.025111  0.0       1        1  51.993961
0     -0.025111  0.0       2        1  48.006042, topic_info=     Category       Freq      Term      Total  loglift  logprob
556   Default  53.000000   tonight  53.000000  30.0000  30.0000
1565  Default  38.000000  thousand  38.000000  29.0000  29.0000
1524  Default  29.000000      lisa  29.000000  28.0000  28.0000
1432  Default  31.000000      lift  31.000000  27.0000  27.0000
283   Default  42.000000      ride  42.000000  26.0000  26.0000
...       ...        ...       ...        ...      ...      ...
12     Topic2  27.666328      caus  59.391640  -0.0301  -5.7955
26     Topic2  26.917191      life  63.786583  -0.1289  -5.8229
74     Topic2  25.512001      away  54.449974  -0.0243  -5.8765
238    Topic2  25.565948      gone  63.895554  -0.1821  -5.8744
42     Topic2  24.465006      babi  54.382484  -0.0650  -5.9184

[173 rows x 6 columns], token_table=      Topic      Freq     Term
term                          
256       1  0.766458      abl
256       2  0.245267      abl
40        1  0.204408  alright
40        2  0.817633  alright
10        1  0.217465   anymor
...     ...       ...      ...
306       2  0.292552    world
1506      1  0.890684    wreck
1506      2  0.127241    wreck
232       1  0.279524     year
232       2  0.711515     year

[254 rows x 3 columns], R=30, lambda_step=0.01, plot_opts={'xlab': 'PC1', 'ylab': 'PC2'}, topic_order=[2, 1])